In [1]:
import os
if "ntbk" in os.getcwd():
    os.chdir("..")
print(os.getcwd())

import sys
sys.path.append(os.path.join(os.getcwd(), "otgnn"))


%load_ext autoreload
%autoreload 2

from otgnn.models import GCN
from otgnn.graph import MolGraph
from otgnn.utils import save_model, load_model

from mol_opt.mol_opt import MolOpt
from mol_opt.data_mol_opt import MolOptDataset
from mol_opt.data_mol_opt import get_loader
from mol_opt.arguments import get_args
from mol_opt.train_mol_opt import main, get_latest_model
from mol_opt.ot_utils import compute_barycenter

from rdkit.Chem import MolFromSmiles

import torch
import numpy as np
import time
import torch.nn.functional as F

/home/octav/gitrepos/tum-thesis


In [2]:
model_type = "deepsets"
sys.argv = ["", "-cuda", "-model_type", model_type]
args = get_args()
outdir_suffix = "dev4"
args.n_epochs = 10000 
args.init_model = "{}-attention-random-sink6-test8".format(model_type)
# args.init_model = "{}-test1".format(model_type)
args.init_decoder_model = "{}_decode".format(args.init_model)
args.output_dir = "mol_opt/output_{}/{}".format(outdir_suffix, args.init_model)
args.tb_logs_dir = "mol_opt/logs_{}/{}".format(outdir_suffix, args.init_model)
args.batch_size = 50 

args.penalty_gumbel = False 

args.scale_lambdas = True
args.connectivity = True 
args.valency = True 
args.euler_characteristic_penalty = True
args.conn_lambda_start = 0.001
args.conn_lambda_end = 3
args.conn_lambda_epochs_start = 1001
args.conn_lambda_epochs_end = 3000
args.valency_lambda_start = 0.001
args.valency_lambda_end = 5
args.valency_lambda_epochs_start = 1001
args.valency_lambda_epochs_end = 3000
args.euler_lambda_start = 0.001 
args.euler_lambda_end = 2 
args.euler_lambda_epochs_start = 1001
args.euler_lambda_epochs_end = 3000
args.tau_start = 1
args.tau_end = 0.01
args.tau_epochs_start = 1
args.tau_epochs_end = 4000

args.cross_att_use = True
args.cross_att_random = True
args.cross_att_n_sinkhorn = 6
# args.morgan_bits = 1024

args.conn_penalty_function = "capped_logdet" 

print(args, '\n')

Namespace(N_transformer=6, agg_func='sum', batch_norm=False, batch_size=50, conn_lambda_end=3, conn_lambda_epochs_end=3000, conn_lambda_epochs_start=1001, conn_lambda_start=0.001, conn_penalty_function='capped_logdet', connectivity=True, connectivity_hard=False, cross_att_dim=150, cross_att_n_sinkhorn=6, cross_att_random=True, cross_att_use=True, cuda=True, device='cuda:0', dim_tangent_space=40, dropout_ffn=0.0, dropout_gcn=0.0, dropout_transformer=0.1, euler_characteristic_penalty=True, euler_lambda_end=2, euler_lambda_epochs_end=3000, euler_lambda_epochs_start=1001, euler_lambda_start=0.001, ffn_activation='LeakyReLU', init_decoder_model='deepsets-attention-random-sink6-test8_decode', init_model='deepsets-attention-random-sink6-test8', linear_out=False, max_num_atoms=70, model_type='deepsets', morgan_bits=0, n_epochs=10000, n_ffn_hidden=100, n_ffn_transformer=100, n_heads_transformer=10, n_hidden=200, n_labels=1, n_layers=5, one_batch_train=False, ot_solver='emd', output_dir='mol_opt

In [3]:
# train_data_loader = get_loader("iclr19-graph2graph/data/qed", "train_pairs", args.batch_size, same_number_atoms = True)
# train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("iclr19-graph2graph/data/qed", "valid", 36, False)

train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("molgen/data/chembl50", "val_split", args.batch_size, same_number_atoms = True)
val_data_loader = None

In [4]:
molopt, molopt_decoder = main(args, train_data_loader = train_data_loader, val_data_loader = val_data_loader)

Found previous model mol_opt/output_dev4/deepsets-attention-random-sink6-test8/model_deepsets-attention-random-sink6-test8_1720, epoch 1720. Overwriting args.
Penalty params: tau=0.13813 conn_l=0.01784 val_l=0.02143 euler_l=0.01541 epoch=1720 mode=[1 1 1] conn=True val=True euler=True
Epoch: 1721


/home/octav/gitrepos/tum-thesis/otgnn/models/gromov_modules.py:398: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.
  nce_reg = torch.nn.LogSoftmax()(torch.stack(all_nce_dists))[0]


Losses Batch 0, train
 fgw:58.1611475
 conn_penalty:87.9488867
 val_penalty:95.4007129
 euler_penalty:37.0440601
 total:62.3455664
Penalty params: tau=0.13797 conn_l=0.01791 val_l=0.02153 euler_l=0.01547 epoch=1721 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.13797 conn_l=0.01791 val_l=0.02153 euler_l=0.01547 epoch=1721 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 1721, train
 fgw:58.1611475
 conn_penalty:87.9488867
 val_penalty:95.4007129
 euler_penalty:37.0440601
 total:62.3455664
Epoch duration: 3.5111730098724365
Epoch: 1722
Losses Batch 0, train
 fgw:18.0815710
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:22.0711597
Penalty params: tau=0.13781 conn_l=0.01798 val_l=0.02162 euler_l=0.01553 epoch=1722 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.13781 conn_l=0.01798 val_l=0.02162 euler_l=0.01553 epoch=1722 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 1722, train
 fgw:18.0815710
 conn_p

Losses Batch 0, train
 fgw:17.5998267
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:21.8204858
Penalty params: tau=0.13561 conn_l=0.01902 val_l=0.02295 euler_l=0.01638 epoch=1736 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.13561 conn_l=0.01902 val_l=0.02295 euler_l=0.01638 epoch=1736 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 1736, train
 fgw:17.5998267
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:21.8204858
Epoch duration: 3.2553789615631104
Epoch: 1737
Losses Batch 0, train
 fgw:17.1995532
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:21.4372192
Penalty params: tau=0.13545 conn_l=0.01909 val_l=0.02305 euler_l=0.01644 epoch=1737 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.13545 conn_l=0.01909 val_l=0.02305 euler_l=0.01644 epoch=1737 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 1737, train
 fgw:17.1995532
 conn

Losses Batch 0, train
 fgw:14.7015637
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:19.1846826
Penalty params: tau=0.13328 conn_l=0.02019 val_l=0.02446 euler_l=0.01734 epoch=1751 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.13328 conn_l=0.02019 val_l=0.02446 euler_l=0.01734 epoch=1751 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 1751, train
 fgw:14.7015637
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:19.1846826
Epoch duration: 4.034307956695557
Epoch: 1752
Losses Batch 0, train
 fgw:14.2955396
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:18.7967249
Penalty params: tau=0.13313 conn_l=0.02028 val_l=0.02457 euler_l=0.01741 epoch=1752 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.13313 conn_l=0.02028 val_l=0.02457 euler_l=0.01741 epoch=1752 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 1752, train
 fgw:14.2955396
 conn_

...

Losses Batch 0, train
 fgw:35.2082788
 conn_penalty:26.0379297
 val_penalty:19.8000000
 euler_penalty:16.2770032
 total:244.8760742
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10751 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10751 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10751, train
 fgw:35.2082788
 conn_penalty:26.0379297
 val_penalty:19.8000000
 euler_penalty:16.2770032
 total:244.8760742
Epoch duration: 3.5268778800964355
Epoch: 10752
Losses Batch 0, train
 fgw:35.5543042
 conn_penalty:25.2634302
 val_penalty:20.1200000
 euler_penalty:17.0788123
 total:246.1022266
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10752 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10752 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10752, train
 fgw:35.554304

Losses Batch 0, train
 fgw:39.8615894
 conn_penalty:15.6390308
 val_penalty:24.9991553
 euler_penalty:26.3590405
 total:264.4925391
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10766 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10766 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10766, train
 fgw:39.8615894
 conn_penalty:15.6390308
 val_penalty:24.9991553
 euler_penalty:26.3590405
 total:264.4925391
Epoch duration: 2.8395845890045166
Epoch: 10767
Losses Batch 0, train
 fgw:39.6470776
 conn_penalty:15.3316577
 val_penalty:24.3192432
 euler_penalty:25.6381494
 total:258.5145703
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10767 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10767 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10767, train
 fgw:39.647077

Saved at mol_opt/output_dev4/deepsets-attention-random-sink6-test8/model_deepsets-attention-random-sink6-test8_10780
Epoch: 10781
Losses Batch 0, train
 fgw:37.9887988
 conn_penalty:16.8683850
 val_penalty:22.7627637
 euler_penalty:19.8137146
 total:242.0351953
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10781 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10781 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10781, train
 fgw:37.9887988
 conn_penalty:16.8683850
 val_penalty:22.7627637
 euler_penalty:19.8137146
 total:242.0351953
Epoch duration: 3.7476541996002197
Epoch: 10782
Losses Batch 0, train
 fgw:38.0087744
 conn_penalty:15.6371082
 val_penalty:22.9199878
 euler_penalty:19.7399243
 total:238.9998828
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10782 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.0

Losses Batch 0, train
 fgw:40.2512524
 conn_penalty:10.0507294
 val_penalty:25.1914600
 euler_penalty:22.1314014
 total:240.6235547
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10796 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10796 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10796, train
 fgw:40.2512524
 conn_penalty:10.0507294
 val_penalty:25.1914600
 euler_penalty:22.1314014
 total:240.6235547
Epoch duration: 3.721719264984131
Epoch: 10797
Losses Batch 0, train
 fgw:39.8938940
 conn_penalty:10.8442773
 val_penalty:25.1800000
 euler_penalty:22.1800000
 total:242.6867188
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10797 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=0.01000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10797 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10797, train
 fgw:39.8938940

KeyboardInterrupt: 